In [2]:
"""
This notebook will train an inception_v3 network to classify STL-10 datasets, based on pretrained
Inception_v3 network on Imagenet dataset

"""

import numpy as np
import tensorflow as tf

import os
import sys
import tarfile
from six.moves import urllib
def reset_graph(seed=42):
    tf.reset_default_graph()
    tf.set_random_seed(seed)
    np.random.seed(seed)


In [3]:
# Path to downloaded checkpoint file
inception_v3_checkpoint_path="C:/Users/caesarliu/Desktop/Tensorflow/datasets/inception/inception_v3.ckpt"
path_to_image='train_X.bin'

In [3]:
def read_all_images(path_to_data):
    """
    :param path_to_data: the file containing the binary images from the STL-10 dataset
    :return: an array containing all the images
    """

    with open(path_to_data, 'rb') as f:
        # read whole file in uint8 chunks
        everything = np.fromfile(f, dtype=np.uint8)

        # We force the data into 3x96x96 chunks, since the
        # images are stored in "column-major order", meaning
        # that "the first 96*96 values are the red channel,
        # the next 96*96 are green, and the last are blue."
        # The -1 is since the size of the pictures depends
        # on the input file, and this way numpy determines
        # the size on its own.

        images = np.reshape(everything, (-1, 3, 96, 96))

        # Now transpose the images into a standard image format
        # readable by, for example, matplotlib.imshow
        # You might want to comment this line or reverse the shuffle
        # if you will use a learning algorithm like CNN, since they like
        # their channels separated.
        images = np.transpose(images, (0, 3, 2, 1))
        return images

In [4]:
def read_labels(path_to_labels):
    """
    :param path_to_labels: path to the binary file containing labels from the STL-10 dataset
    :return: an array containing the labels
    """
    with open(path_to_labels, 'rb') as f:
        labels = np.fromfile(f, dtype=np.uint8)
        return labels


In [5]:
train_X=read_all_images('train_X.bin')
train_Y=read_labels('train_y.bin')
test_X=read_all_images('test_X.bin')
test_Y=read_labels('test_y.bin')

In [6]:
from scipy.misc import imresize

def prepare_image(image, target_width = 299, target_height = 299, max_zoom = 0.2):
    """Preprocessing the images to the from expected by the network."""

    height = image.shape[0]
    width = image.shape[1]
    image_ratio = width / height
    target_image_ratio = target_width / target_height
    crop_vertically = image_ratio < target_image_ratio
    crop_width = width if crop_vertically else int(height * target_image_ratio)
    crop_height = int(width / target_image_ratio) if crop_vertically else height
        

    resize_factor = np.random.rand() * max_zoom + 1.0
    crop_width = int(crop_width / resize_factor)
    crop_height = int(crop_height / resize_factor)
    

    x0 = np.random.randint(0, width - crop_width)
    y0 = np.random.randint(0, height - crop_height)
    x1 = x0 + crop_width
    y1 = y0 + crop_height
    

    image = image[y0:y1, x0:x1]

    # flip the image horizontally with 50% probability:
    if np.random.rand() < 0.5:
        image = np.fliplr(image)

    # Resize the image to the target dimensions.
    image = imresize(image, (target_width, target_height))
    

    return image.astype(np.float32) / 255

In [4]:
"""
Load pre_trained inception_v3 network

"""

from tensorflow.contrib.slim.nets import inception
import tensorflow.contrib.slim as slim

reset_graph()

X = tf.placeholder(tf.float32, shape=[None, 299, 299, 3], name='X')
training = tf.placeholder_with_default(False, shape=[])
with slim.arg_scope(inception.inception_v3_arg_scope()):
    logits, end_points = inception.inception_v3(X, num_classes=1001, is_training=training)

inception_saver = tf.train.Saver()

In [5]:
# Visualize the computational graph

from IPython.display import clear_output, Image, display, HTML
def strip_consts(graph_def, max_const_size=32):
    """Strip large constant values from graph_def."""
    strip_def = tf.GraphDef()
    for n0 in graph_def.node:
        n = strip_def.node.add() 
        n.MergeFrom(n0)
        if n.op == 'Const':
            tensor = n.attr['value'].tensor
            size = len(tensor.tensor_content)
            if size > max_const_size:
                tensor.tensor_content = tf.compat.as_bytes("<stripped %d bytes>"%size)
    return strip_def


def show_graph(graph_def, max_const_size=32):
    """Visualize TensorFlow graph."""
    if hasattr(graph_def, 'as_graph_def'):
        graph_def = graph_def.as_graph_def()
    strip_def = strip_consts(graph_def, max_const_size=max_const_size)
    code = """
        <script>
          function load() {{
            document.getElementById("{id}").pbtxt = {data};
          }}
        </script>
        <link rel="import" href="https://tensorboard.appspot.com/tf-graph-basic.build.html" onload=load()>
        <div style="height:600px">
          <tf-graph-basic id="{id}"></tf-graph-basic>
        </div>
    """.format(data=repr(str(strip_def)), id='graph'+str(np.random.rand()))
  
    iframe = """
        <iframe seamless style="width:800px;height:620px;border:0" srcdoc="{}"></iframe>
    """.format(code.replace('"', '&quot;'))
    display(HTML(iframe))

show_graph(tf.get_default_graph())

In [6]:
end_points # model layers

{'AuxLogits': <tf.Tensor 'InceptionV3/AuxLogits/SpatialSqueeze:0' shape=(?, 1001) dtype=float32>,
 'Conv2d_1a_3x3': <tf.Tensor 'InceptionV3/InceptionV3/Conv2d_1a_3x3/Relu:0' shape=(?, 149, 149, 32) dtype=float32>,
 'Conv2d_2a_3x3': <tf.Tensor 'InceptionV3/InceptionV3/Conv2d_2a_3x3/Relu:0' shape=(?, 147, 147, 32) dtype=float32>,
 'Conv2d_2b_3x3': <tf.Tensor 'InceptionV3/InceptionV3/Conv2d_2b_3x3/Relu:0' shape=(?, 147, 147, 64) dtype=float32>,
 'Conv2d_3b_1x1': <tf.Tensor 'InceptionV3/InceptionV3/Conv2d_3b_1x1/Relu:0' shape=(?, 73, 73, 80) dtype=float32>,
 'Conv2d_4a_3x3': <tf.Tensor 'InceptionV3/InceptionV3/Conv2d_4a_3x3/Relu:0' shape=(?, 71, 71, 192) dtype=float32>,
 'Logits': <tf.Tensor 'InceptionV3/Logits/SpatialSqueeze:0' shape=(?, 1001) dtype=float32>,
 'MaxPool_3a_3x3': <tf.Tensor 'InceptionV3/InceptionV3/MaxPool_3a_3x3/MaxPool:0' shape=(?, 73, 73, 64) dtype=float32>,
 'MaxPool_5a_3x3': <tf.Tensor 'InceptionV3/InceptionV3/MaxPool_5a_3x3/MaxPool:0' shape=(?, 35, 35, 192) dtype=floa

In [9]:

# Select the layer which will be retrained with the training data in STL-10 dataset
prelogit=tf.squeeze(end_points['PreLogits'],axis=[1,2])

In [10]:
# Build the model
n_outputs=10

with tf.name_scope('new_output_layer'):
    stl_logits=tf.layers.dense(prelogit,n_outputs,name='stl_logits')
    Y_proba=tf.nn.softmax(stl_logits,name='Proba')

In [11]:
y=tf.placeholder(tf.int32,shape=[None])


with tf.name_scope('train'):
    entropy=tf.nn.sparse_softmax_cross_entropy_with_logits(logits=stl_logits,labels=y)
    loss=tf.reduce_mean(entropy)
    optimizer=tf.train.AdamOptimizer()
    Vars=tf.get_collection(tf.GraphKeys.TRAINABLE_VARIABLES, scope='stl_logits')
    training_op=optimizer.minimize(loss,var_list=Vars)

with tf.name_scope('eval'):
    correct=tf.nn.in_top_k(stl_logits,y,1)
    accuracy=tf.reduce_mean(tf.cast(correct,tf.float32))
    
with tf.name_scope('init_and_save'):
    init=tf.global_variables_initializer()
    saver=tf.train.Saver()

In [2]:
from random import sample

def prepare_batch(X,Y,batch_size):
    
    """
    Funtion to load images batch by batch
    
    """
    length=len(Y)
    Index=list(range(length))
    sampled_index=sample(Index,batch_size)
    sampled_images=X[sampled_index,:,:,:]
    prepared_images=[prepare_image(image) for image in sampled_images]
    x_batch=np.stack(prepared_images)
    y_batch=Y[sampled_index]
    return x_batch,y_batch  

In [13]:
# Preprocess test sets
X_test,Y_test=prepare_batch(test_X,test_Y,8000)

In [15]:
# Traina and Evaluate the model

n_epochs=10
batch_size=50
n_iterations_per_epoch=100

with tf.Session() as sess:
    init.run()
    inception_saver.restore(sess,inception_v3_checkpoint_path)
    
    for epoch in range(n_epochs):
        print('Epoch',epoch, end='')
        for iteration in range(n_iterations_per_epoch):
            print('.',end='')
            x_batch,y_batch=prepare_batch(train_X,train_Y,batch_size)
            y_eval=y_batch-1 
            sess.run(training_op, feed_dict={X:x_batch,y:y_eval})  
        acc_train=accuracy.eval(feed_dict={X:x_batch,y:y_eval})
        print(' Train accuracy:', acc_train)
        
        save_path=saver.save(sess,  './Save/STL_10')
    Y_eval=Y_test-1
    print('Computing final accuracy on the test set...')
    test_ac=np.zeros((1,100))
    for i in range(100):
        acc_test = accuracy.eval(feed_dict={X: X_test[i*80:(i+1)*80,:,:,:], y: Y_eval[i*80:(i+1)*80]})
        test_ac[:,i]=acc_test
    print('Test accuracy:', np.mean(test_ac))

Epoch 0.................................................................................................... Train accuracy: 1.0
Epoch 1.................................................................................................... Train accuracy: 0.98
Epoch 2.................................................................................................... Train accuracy: 0.96
Epoch 3.................................................................................................... Train accuracy: 1.0
Epoch 4.................................................................................................... Train accuracy: 1.0
Epoch 5.................................................................................................... Train accuracy: 1.0
Epoch 6.................................................................................................... Train accuracy: 1.0
Epoch 7...............................................................................................